Install Requirements and Depedencies, Also login to huggingface through command line

In [1]:
!pip install datasets==1.18.3
!pip install transformers
!pip install pyctcdecode
!pip install jiwer
!pip install https://github.com/kpu/kenlm/archive/master.zip
!huggingface-cli login

     |████████████████████████████████| 311 kB 5.1 MB/s 
     |████████████████████████████████| 67 kB 5.1 MB/s 
     |████████████████████████████████| 1.1 MB 52.3 MB/s 
     |████████████████████████████████| 133 kB 52.1 MB/s 
     |████████████████████████████████| 243 kB 52.3 MB/s 
     |████████████████████████████████| 144 kB 60.9 MB/s 
     |████████████████████████████████| 271 kB 47.4 MB/s 
     |████████████████████████████████| 94 kB 1.8 MB/s 
     |████████████████████████████████| 3.5 MB 5.8 MB/s 
     |████████████████████████████████| 895 kB 53.6 MB/s 
     |████████████████████████████████| 596 kB 59.6 MB/s 
     |████████████████████████████████| 6.8 MB 50.5 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
     |████████████████████████████████| 43 kB 1.2 MB/s 
     |████████████████████████████████| 376 kB 10.3 MB/s 
  Created wheel for pygtrie: filename=pygtrie-2

#### Preprocessing Data, initialize loss function and evaluation function that edited from based on [This Github Repo](https://github.com/harveenchadha/bol/blob/main/demos/robus/evaluate_model_hf_with_lm.ipynb)

In [2]:
import torch
import torchaudio
from datasets import load_dataset, load_metric,  Audio
from transformers import Wav2Vec2ForCTC, Wav2Vec2Processor, Wav2Vec2ProcessorWithLM
import re
wer = load_metric("wer")
cer = load_metric("cer")


chars_to_ignore_regex = '[\é\！\，\,\?\.\!\-\;\:\"\“\%\‘\”\�\'\’\—\–\·]'

def load_data(dataset_id, language, split='test'):
    test_dataset = load_dataset(dataset_id, language, split=split, use_auth_token=True)
    test_dataset = test_dataset.cast_column("audio", Audio(sampling_rate=16_000))
    return test_dataset

def speech_file_to_array_fn(batch):
    batch["sentence"] = re.sub(chars_to_ignore_regex, "", batch["sentence"]).lower() + " "
    batch["sentence"] = re.sub('!', '', batch["sentence"]).lower() + " "
    batch["sentence"] = batch["sentence"].replace('\"',"").replace("&","").replace("'","").replace("(","").lower() + " "
    batch["sentence"] = batch["sentence"].replace('[',"").replace("]","").replace("\\","").replace("«","").replace("»","").replace(")","").lower() + " "
    batch["sentence"] = batch["sentence"].replace("  "," ").replace("  "," ").replace("  "," ").lower() + " "
    
    batch["speech"] = batch["audio"]["array"]
    return batch


def evaluate_with_lm(batch):
    inputs = processor(batch["speech"], sampling_rate=16_000, return_tensors="pt", padding=True)

    with torch.no_grad():
        logits = model(**inputs.to('cuda')).logits
    int_result = processor.batch_decode(logits.cpu().numpy())

    batch["pred_strings"] =  int_result.text

    del int_result
    torch.cuda.empty_cache()

    return batch

def evaluate(batch):

    inputs = processor(batch["speech"], sampling_rate=16_000, return_tensors="pt", padding=True)
    with torch.no_grad():
        logits = model(inputs.input_values.to('cuda')).logits

    pred_ids = torch.argmax(logits, dim=-1)
    batch["pred_strings"] = processor.batch_decode(pred_ids, skip_special_tokens=True)
    return batch


Downloading:   0%|          | 0.00/1.90k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.16k [00:00<?, ?B/s]

### Evaluate using language model
Results: <br>
WER: 0.086074 (8.6074) <br>
CER: 0.024147 (2.4147)

In [3]:
import torch
import torchaudio
from datasets import load_dataset, load_metric,  Audio
from transformers import Wav2Vec2ForCTC, Wav2Vec2Processor, Wav2Vec2ProcessorWithLM
import re

language="ia"
model_id = 'ayameRushia/wav2vec2-large-xls-r-300m-ia'
dataset_id = "mozilla-foundation/common_voice_8_0"
split="test"

processor = Wav2Vec2ProcessorWithLM.from_pretrained(model_id,use_auth_token=True)
model = Wav2Vec2ForCTC.from_pretrained(model_id,use_auth_token=True)
model.to('cuda')

test_dataset = load_data(dataset_id, language, split)
test_dataset = test_dataset.map(speech_file_to_array_fn)

result = test_dataset.map(evaluate_with_lm, batched=True, batch_size=4)

print("WER: {:2f}".format(wer.compute(predictions=result["pred_strings"], references=result["sentence"])))
print("CER: {:2f}".format(cer.compute(predictions=result["pred_strings"], references=result["sentence"])))

Downloading:   0%|          | 0.00/262 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/344 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/269 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/502 [00:00<?, ?B/s]

...

0 examples [00:00, ? examples/s]

Dataset common_voice downloaded and prepared to /root/.cache/huggingface/datasets/mozilla-foundation___common_voice/ia/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8. Subsequent calls will reuse this data.


0ex [00:00, ?ex/s]

  0%|          | 0/427 [00:00<?, ?ba/s]

WER: 0.086074
CER: 0.024147


Delete previous model and clear the cuda cache

In [4]:
del model
torch.cuda.empty_cache()
!nvidia-smi

Sun Feb  6 06:38:45 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   77C    P0    38W /  70W |   2810MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

### Evaluate without using language model
Results: <br>
WER: 0.201776 (20.1776) <br>
CER: 0.047205 (4.7205) <br>

In [6]:
dataset_id = "mozilla-foundation/common_voice_8_0"
language="ia"
split="test"
model_id = 'ayameRushia/wav2vec2-large-xls-r-300m-ia'

processor = Wav2Vec2Processor.from_pretrained(model_id,use_auth_token=True)
model = Wav2Vec2ForCTC.from_pretrained(model_id,use_auth_token=True)
model.to("cuda")

test_dataset = load_data(dataset_id, language, split)
test_dataset = test_dataset.map(speech_file_to_array_fn)

result = test_dataset.map(evaluate, batched=True, batch_size=4)

print("WER: {:2f}".format(wer.compute(predictions=result["pred_strings"], references=result["sentence"])))
print("CER: {:2f}".format(cer.compute(predictions=result["pred_strings"], references=result["sentence"])))

Reusing dataset common_voice (/root/.cache/huggingface/datasets/mozilla-foundation___common_voice/ia/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Loading cached processed dataset at /root/.cache/huggingface/datasets/mozilla-foundation___common_voice/ia/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8/cache-f4febe81b8fd7934.arrow


  0%|          | 0/427 [00:00<?, ?ba/s]

WER: 0.201776
CER: 0.047205
